# Using KNN, SVM, Naive Bayes on the Means of the Channels as Features 
Like from the paper: http://www.cs.cmu.edu/~kkchang/paper/WangEtAl.2013.AIED.EEG-MOOC.pdf


In [1]:
# import the toolboxes 
import numpy as np 
import pandas as pd
import os
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import LinearSVC
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold
from tqdm import tqdm
# import sklearn logistic regression
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.linear_model import BayesianRidge
from sklearn.feature_selection import SelectFromModel
from sklearn.kernel_approximation import RBFSampler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from sklearn.model_selection import KFold

In [2]:
#directory = '/Users/amandabreton/Documents/Duke 2022-2023/ECE 590/Final Project/'
filename = 'meanfeatures.csv'

#df = pd.read_csv(directory+filename, index_col=0)
df = pd.read_csv('cleaned_data/meanfeatures.csv', index_col=0)

In [3]:
df.head()

SubjectID  VideoID  user-definedlabel  Attention  Mediation        Raw   
0        0.0      0.0                0.0  55.256944  53.826389  46.986111  \
1        0.0      1.0                1.0  43.621429  48.621429  28.800000   
2        0.0      2.0                1.0  43.978873  47.316901  13.154930   
3        0.0      3.0                0.0  51.057377  51.844262  34.713115   
4        0.0      4.0                0.0  55.224138  47.474138  30.008621   

           Delta          Theta        Alpha1        Alpha2         Beta1   
0  544315.097222  124965.590278  36693.701389  25875.298611  20108.791667  \
1  739737.292857  161064.228571  34918.028571  25078.935714  22157.307143   
2  694078.084507  149816.873239  30493.873239  21667.591549  21888.338028   
3  600823.688525  162653.360656  33367.278689  26281.500000  17224.278689   
4  546628.017241  126893.948276  23113.844828  17017.051724  15955.879310   

          Beta2        Gamma1        Gamma2  
0  40268.763889  40729.284722  16817.062500  
1  37410.728571  36758.700000  14519.407143  
2  36446.436620  33908.873239  14545.845070  
3  43706.524590  41438.213115  16558.631148  
4  36427.836207  36024.818966  14752.655172

In [4]:
df.shape

(100, 14)

In [5]:
X = df.drop(['SubjectID', 'VideoID', 'user-definedlabel'], axis=1)
X.head()

Attention  Mediation        Raw          Delta          Theta   
0  55.256944  53.826389  46.986111  544315.097222  124965.590278  \
1  43.621429  48.621429  28.800000  739737.292857  161064.228571   
2  43.978873  47.316901  13.154930  694078.084507  149816.873239   
3  51.057377  51.844262  34.713115  600823.688525  162653.360656   
4  55.224138  47.474138  30.008621  546628.017241  126893.948276   

         Alpha1        Alpha2         Beta1         Beta2        Gamma1   
0  36693.701389  25875.298611  20108.791667  40268.763889  40729.284722  \
1  34918.028571  25078.935714  22157.307143  37410.728571  36758.700000   
2  30493.873239  21667.591549  21888.338028  36446.436620  33908.873239   
3  33367.278689  26281.500000  17224.278689  43706.524590  41438.213115   
4  23113.844828  17017.051724  15955.879310  36427.836207  36024.818966   

         Gamma2  
0  16817.062500  
1  14519.407143  
2  14545.845070  
3  16558.631148  
4  14752.655172

In [6]:
y = df[['user-definedlabel']]
y.head()

user-definedlabel
0                0.0
1                1.0
2                1.0
3                0.0
4                0.0

In [7]:
y = y['user-definedlabel'].values
y.shape


(100,)

In [8]:
np.logspace(-11,6,18)

array([1.e-11, 1.e-10, 1.e-09, 1.e-08, 1.e-07, 1.e-06, 1.e-05, 1.e-04,
       1.e-03, 1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03, 1.e+04,
       1.e+05, 1.e+06])

In [9]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3)

In [10]:
def pick_model(model_type, C=1,verb=False):
    if model_type == 'logreg':
        clf = LogisticRegression()
        param_grid = {"C": [0.1, 1, 10, 100], "penalty": ["l1", "l2"], "solver": ["liblinear"]}
    elif model_type == 'rvm':
        clf = BayesianRidge(compute_score=True)
        param_grid = {"alpha_1": [1e-6, 1e-5, 1e-4, 1e-3], "alpha_2": [1e-6, 1e-5, 1e-4, 1e-3], "lambda_1": [1e-6, 1e-5, 1e-4, 1e-3], "lambda_2": [1e-6, 1e-5, 1e-4, 1e-3]}
    elif model_type == 'forest': # model_type = random forest
        clf = RandomForestClassifier()
        param_grid = {"n_estimators": [10, 50, 100, 200, 500, 1000], "max_depth": [None, 5, 10, 20, 50, 100]}
    return clf, param_grid


In [11]:
# need to do cross fold validation --> grid search for best parameters
#num_splits = KFold(n_splits=10,shuffle = True)
#for train_index, test_index in tqdm(num_splits.split(X)): # to actually split into training/testing
#    X_train, X_test = X[train_index], X[test_index]
#    y_train, y_test = y[train_index], y[test_index]
    

# questions for alex: 
* we should probably do some sort of optimization of parameters? --. yes use grid search
* i only skimmed the paper but it seems like they only used means of each channel as the features so i guess we can just stick w/ that for this week, and then work on using better features next week? 
* do you want to plan to work on the decision tree classifier on like thursday/friday? 
* thinking we should probably work on the paper and presentation Monday/Tuesday next week, finish up by

grid search better --> 2 levels 
grid search CV 
target = user defined labels
check if they standardized/normalized the data --> we should probably do it in case it adds to computation time for grid search cv 
reconnect tomorrow 

In [12]:
from warnings import simplefilter
from sklearn.exceptions import ConvergenceWarning
simplefilter("ignore", category=ConvergenceWarning)

In [13]:
# Define the hyperparameters you want to tune and their respective values
#Cs = np.logspace(-11,6,18)
#param_grid = {"C": Cs, "penalty": ["l1", "l2"]}

# Create an instance of the  model
model, param_grid = pick_model(model_type = 'logreg')

# Create an instance of the GridSearchCV object
grid_search = GridSearchCV(model, param_grid, cv=5, scoring="accuracy")

# Fit the GridSearchCV object to the data
grid_search.fit(X, y)

# Print the best hyperparameters and their accuracy score
print("Best Hyperparameters:", grid_search.best_params_)
print("Best Accuracy Score:", grid_search.best_score_)

# Use the best hyperparameters to train and test the model
best_log_reg = grid_search.best_estimator_
best_log_reg.fit(X_train, y_train)
y_pred = best_log_reg.predict(X_test)
acc = accuracy_score(y_test, y_pred)
print('test accuracy:', acc)

Best Hyperparameters: {'C': 1, 'penalty': 'l2', 'solver': 'liblinear'}
Best Accuracy Score: 0.69
test accuracy: 0.6333333333333333


In [14]:
# need to do 2 levels of cross validation?
# first level of cross validation being used to optimize accuracy
# and the second level being used to find the optimal parameters --> grid search through the training set

In [15]:
# first level: for optimizing accuracy 

num_splits = KFold(n_splits=5,shuffle = True)
for train_index, test_index in tqdm(num_splits.split(X)): # to actually split into training/testing
    #X.iloc[0].values
    X_train, X_test = X.iloc[train_index].values, X.iloc[test_index].values
    y_train, y_test = y[train_index], y[test_index]
    num_splits_2 = KFold(n_splits=5,shuffle = True) 
    # Create an instance of the  model
    model, param_grid = pick_model(model_type = 'logreg')
    # Create an instance of the GridSearchCV object
    grid_search = GridSearchCV(model, param_grid, cv=5, scoring="accuracy")
    # Fit the GridSearchCV object to the data
    grid_search.fit(X_train, y_train)
    # Print the best hyperparameters and their accuracy score
    print("Best Hyperparameters:", grid_search.best_params_)
    print("Best Accuracy Score:", grid_search.best_score_)     

2it [00:00,  6.86it/s]

Best Hyperparameters: {'C': 0.1, 'penalty': 'l2', 'solver': 'liblinear'}
Best Accuracy Score: 0.7
Best Hyperparameters: {'C': 10, 'penalty': 'l1', 'solver': 'liblinear'}
Best Accuracy Score: 0.675


4it [00:00,  7.51it/s]

Best Hyperparameters: {'C': 0.1, 'penalty': 'l1', 'solver': 'liblinear'}
Best Accuracy Score: 0.675
Best Hyperparameters: {'C': 0.1, 'penalty': 'l2', 'solver': 'liblinear'}
Best Accuracy Score: 0.6375


5it [00:00,  7.37it/s]

Best Hyperparameters: {'C': 0.1, 'penalty': 'l1', 'solver': 'liblinear'}
Best Accuracy Score: 0.6375


In [16]:
# making a function for 2 level cross validation: 
# first level: for optimizing accuracy 
def twolevelCV(X,y,verb=False, model_type = 'svm'):
    num_splits = KFold(n_splits=5,shuffle = True)
    for train_index, test_index in tqdm(num_splits.split(X)): # to actually split into training/testing
        #X.iloc[0].values
        X_train, X_test = X.iloc[train_index].values, X.iloc[test_index].values
        y_train, y_test = y[train_index], y[test_index]
        num_splits_2 = KFold(n_splits=5,shuffle = True) 
        # Create an instance of the  model
        model, param_grid = pick_model(model_type)
        # Create an instance of the GridSearchCV object
        grid_search = GridSearchCV(model, param_grid, cv=5, scoring="accuracy")
        # Fit the GridSearchCV object to the data
        grid_search.fit(X_train, y_train)
        # Print the best hyperparameters and their accuracy score
        print("Training: Best Hyperparameters:", grid_search.best_params_)
        print("Training: Best Accuracy Score:", grid_search.best_score_)
        best_est = grid_search.best_estimator_
        best_est.fit(X_train, y_train)
        y_pred = best_log_reg.predict(X_test)
        acc = accuracy_score(y_test, y_pred)
        print('Test accuracy:', acc)

In [17]:
twolevelCV(X,y,model_type = 'logreg')

0it [00:00, ?it/s]/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
1it [00:00,  8.00it/s]

Training: Best Hyperparameters: {'C': 100, 'penalty': 'l1', 'solver': 'liblinear'}
Training: Best Accuracy Score: 0.6625
Test accuracy: 0.7
Training: Best Hyperparameters: {'C': 1, 'penalty': 'l1', 'solver': 'liblinear'}
Training: Best Accuracy Score: 0.7375


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
2it [00:00,  5.88it/s]/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
3it [00:00,  5.94it/s]

Test accuracy: 0.6
Training: Best Hyperparameters: {'C': 100, 'penalty': 'l2', 'solver': 'liblinear'}
Training: Best Accuracy Score: 0.65
Test accuracy: 0.85


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
4it [00:00,  6.64it/s]/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
5it [00:00,  6.62it/s]

Training: Best Hyperparameters: {'C': 1, 'penalty': 'l1', 'solver': 'liblinear'}
Training: Best Accuracy Score: 0.7125
Test accuracy: 0.8
Training: Best Hyperparameters: {'C': 0.1, 'penalty': 'l1', 'solver': 'liblinear'}
Training: Best Accuracy Score: 0.625
Test accuracy: 0.8


In [18]:
twolevelCV(X,y,model_type = 'rvm')

0it [00:00, ?it/s]/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:778: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 234, in __call__
    return self._score(
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 282, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/utils/_param_validation.py", line 192, in wrapper
    return func(*args, **kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py",

Training: Best Hyperparameters: {'alpha_1': 1e-06, 'alpha_2': 1e-06, 'lambda_1': 1e-06, 'lambda_2': 1e-06}
Training: Best Accuracy Score: nan
Test accuracy: 0.6


/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:778: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 234, in __call__
    return self._score(
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 282, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/utils/_param_validation.py", line 192, in wrapper
    return func(*args, **kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py", line 221, in accu

Training: Best Hyperparameters: {'alpha_1': 1e-06, 'alpha_2': 1e-06, 'lambda_1': 1e-06, 'lambda_2': 1e-06}
Training: Best Accuracy Score: nan
Test accuracy: 0.8


/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:778: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 234, in __call__
    return self._score(
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 282, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/utils/_param_validation.py", line 192, in wrapper
    return func(*args, **kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py", line 221, in accu

Training: Best Hyperparameters: {'alpha_1': 1e-06, 'alpha_2': 1e-06, 'lambda_1': 1e-06, 'lambda_2': 1e-06}
Training: Best Accuracy Score: nan
Test accuracy: 0.85


/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:778: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 234, in __call__
    return self._score(
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 282, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/utils/_param_validation.py", line 192, in wrapper
    return func(*args, **kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py", line 221, in accu

Training: Best Hyperparameters: {'alpha_1': 1e-06, 'alpha_2': 1e-06, 'lambda_1': 1e-06, 'lambda_2': 1e-06}
Training: Best Accuracy Score: nan
Test accuracy: 0.75


/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py:778: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/model_selection/_validation.py", line 767, in _score
    scores = scorer(estimator, X_test, y_test)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 234, in __call__
    return self._score(
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_scorer.py", line 282, in _score
    return self._sign * self._score_func(y_true, y_pred, **self._kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/utils/_param_validation.py", line 192, in wrapper
    return func(*args, **kwargs)
  File "/home/codespace/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py", line 221, in accu

Training: Best Hyperparameters: {'alpha_1': 1e-06, 'alpha_2': 1e-06, 'lambda_1': 1e-06, 'lambda_2': 1e-06}
Training: Best Accuracy Score: nan
Test accuracy: 0.75


In [19]:
twolevelCV(X,y,model_type = 'forest')

0it [00:00, ?it/s]/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
1it [01:13, 73.27s/it]

Training: Best Hyperparameters: {'max_depth': 20, 'n_estimators': 10}
Training: Best Accuracy Score: 0.775
Test accuracy: 0.75
Training: Best Hyperparameters: {'max_depth': 20, 'n_estimators': 1000}
Training: Best Accuracy Score: 0.75


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
2it [02:27, 74.09s/it]

Test accuracy: 0.85
Training: Best Hyperparameters: {'max_depth': None, 'n_estimators': 200}
Training: Best Accuracy Score: 0.775


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
3it [03:40, 73.30s/it]

Test accuracy: 0.7


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
4it [04:52, 72.67s/it]

Training: Best Hyperparameters: {'max_depth': 50, 'n_estimators': 10}
Training: Best Accuracy Score: 0.7875
Test accuracy: 0.8
Training: Best Hyperparameters: {'max_depth': None, 'n_estimators': 500}
Training: Best Accuracy Score: 0.8


/home/codespace/.local/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
5it [06:05, 73.03s/it]

Test accuracy: 0.65
